In [63]:
!rm -rf /content/ChatTTS
!git clone https://github.com/2noise/ChatTTS.git
!pip install -r /content/ChatTTS/requirements.txt
!pip install nemo_text_processing WeTextProcessing
!ldconfig /usr/lib64-nvidia

Cloning into 'ChatTTS'...
remote: Enumerating objects: 168, done.
remote: Counting objects: 100% (130/130), done.
remote: Compressing objects: 100% (82/82), done.
remote: Total 168 (delta 92), reused 48 (delta 48), pack-reused 38
Receiving objects: 100% (168/168), 2.73 MiB | 6.07 MiB/s, done.
Resolving deltas: 100% (93/93), done.
/sbin/ldconfig.real: /usr/local/lib/libtbbmalloc.so.2 is not a symbolic link

/sbin/ldconfig.real: /usr/local/lib/libtbbbind_2_0.so.3 is not a symbolic link

/sbin/ldconfig.real: /usr/local/lib/libtbbbind.so.3 is not a symbolic link

/sbin/ldconfig.real: /usr/local/lib/libtbb.so.12 is not a symbolic link

/sbin/ldconfig.real: /usr/local/lib/libtbbmalloc_proxy.so.2 is not a symbolic link

/sbin/ldconfig.real: /usr/local/lib/libtbbbind_2_5.so.3 is not a symbolic link



In [64]:
import torch
torch._dynamo.config.cache_size_limit = 64
torch._dynamo.config.suppress_errors = True
torch.set_float32_matmul_precision('high')

from ChatTTS import ChatTTS
from IPython.display import Audio

## Load Models

In [65]:
chat = ChatTTS.Chat()

# Use force_redownload=True if the weights updated.
chat.load_models(force_redownload=True)

# If you download the weights manually, set source='locals'.
# chat.load_models(source='local', local_path='YOUR LOCAL PATH')

Fetching 11 files:   0%|          | 0/11 [00:00<?, ?it/s]

## Inference

### Batch infer

In [68]:
texts = ["So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with.",]*3 \
        + ["我觉得像我们这些写程序的人，他，我觉得多多少少可能会对开源有一种情怀在吧我觉得开源是一个很好的形式。现在其实最先进的技术掌握在一些公司的手里的话，就他们并不会轻易的开放给所有的人用。"]*3

wavs = chat.infer(texts)

2024-06-09 08:45:12,963 WETEXT INFO found existing fst: /usr/local/lib/python3.10/dist-packages/tn/zh_tn_tagger.fst
2024-06-09 08:45:12,963 WETEXT INFO found existing fst: /usr/local/lib/python3.10/dist-packages/tn/zh_tn_tagger.fst
INFO:wetext-zh_normalizer:found existing fst: /usr/local/lib/python3.10/dist-packages/tn/zh_tn_tagger.fst
2024-06-09 08:45:12,970 WETEXT INFO                     /usr/local/lib/python3.10/dist-packages/tn/zh_tn_verbalizer.fst
2024-06-09 08:45:12,970 WETEXT INFO                     /usr/local/lib/python3.10/dist-packages/tn/zh_tn_verbalizer.fst
INFO:wetext-zh_normalizer:                    /usr/local/lib/python3.10/dist-packages/tn/zh_tn_verbalizer.fst
2024-06-09 08:45:12,975 WETEXT INFO skip building fst for zh_normalizer ...
2024-06-09 08:45:12,975 WETEXT INFO skip building fst for zh_normalizer ...
INFO:wetext-zh_normalizer:skip building fst for zh_normalizer ...
 49%|████▉     | 1012/2048 [00:33<00:34, 30.11it/s]


In [69]:
Audio(wavs[0], rate=24_000, autoplay=True)

In [70]:
Audio(wavs[3], rate=24_000, autoplay=True)

### Custom params

In [71]:
params_infer_code = {'prompt':'[speed_5]', 'temperature':.3}
params_refine_text = {'prompt':'[oral_2][laugh_0][break_6]'}

wav = chat.infer('四川美食可多了，有麻辣火锅、宫保鸡丁、麻婆豆腐、担担面、回锅肉、夫妻肺片等，每样都让人垂涎三尺。', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)

 19%|█▊        | 379/2048 [00:11<00:50, 32.93it/s]


In [72]:
Audio(wav[0], rate=24_000, autoplay=True)

### fix random speaker

In [73]:
rand_spk = chat.sample_random_speaker()
params_infer_code = {'spk_emb' : rand_spk, }

wav = chat.infer('四川美食确实以辣闻名，但也有不辣的选择。比如甜水面、赖汤圆、蛋烘糕、叶儿粑等，这些小吃口味温和，甜而不腻，也很受欢迎。', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)

 28%|██▊       | 573/2048 [00:16<00:43, 33.80it/s]


In [75]:
Audio(wav[0], rate=24_000, autoplay=True)

### Two stage control

In [76]:
text = "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with."
refined_text = chat.infer(text, refine_text_only=True)
refined_text

 21%|██        | 80/384 [00:02<00:09, 31.78it/s]


['so we found being competitive and collaborative [uv_break] was a huge way of staying motivated towards our goals, [uv_break] so one person to call when you fall off, one person who gets you back on [uv_break] then one person to actually do the activity with.']

In [77]:
wav = chat.infer(refined_text)

 42%|████▏     | 850/2048 [00:26<00:36, 32.48it/s]


In [78]:
Audio(wav[0], rate=24_000, autoplay=True)

In [79]:
text = 'so we found being competitive and collaborative [uv_break] was a huge way of staying [uv_break] motivated towards our goals, [uv_break] so [uv_break] one person to call [uv_break] when you fall off, [uv_break] one person who [uv_break] gets you back [uv_break] on then [uv_break] one person [uv_break] to actually do the activity with.'
wav = chat.infer(text, skip_refine_text=True)

 51%|█████     | 1047/2048 [00:31<00:29, 33.52it/s]


In [80]:
Audio(wav[0], rate=24_000, autoplay=True)

## LLM Call

In [ ]:
from ChatTTS.experimental.llm import llm_api

API_KEY = ''
client = llm_api(api_key=API_KEY,
        base_url="https://api.deepseek.com",
        model="deepseek-chat")

In [ ]:
user_question = '四川有哪些好吃的美食呢?'
text = client.call(user_question, prompt_version = 'deepseek')
print(text)
text = client.call(text, prompt_version = 'deepseek_TN')
print(text)

In [ ]:
params_infer_code = {'spk_emb' : rand_spk, 'temperature':.3}

wav = chat.infer(text, params_infer_code=params_infer_code)